In [ ]:
import pandas as pd

df_corpus = pd.read_json("hf://datasets/mteb/msmarco/corpus.jsonl", lines=True)

df_queries = pd.read_json("hf://datasets/mteb/msmarco/queries.jsonl", lines=True)

splits = {'train': 'qrels/train.jsonl', 'dev': 'qrels/dev.jsonl', 'test': 'qrels/test.jsonl'}
df_qrels_train = pd.read_json("hf://datasets/mteb/msmarco/" + splits["train"], lines=True)
df_qrels_dev = pd.read_json("hf://datasets/mteb/msmarco/" + splits["dev"], lines=True)
df_qrels_test = pd.read_json("hf://datasets/mteb/msmarco/" + splits["test"], lines=True)

In [ ]:
df_corpus

_id title                                               text
0              0        The presence of communication amid scientific ...
1              1        The Manhattan Project and its atomic bomb help...
2              2        Essay on The Manhattan Project - The Manhattan...
3              3        The Manhattan Project was the name for a proje...
4              4        versions of each volume as well as complementa...
...          ...   ...                                                ...
8841818  8841818        When metal salts emit short wavelengths of vis...
8841819  8841819        Thousands of people across the United States w...
8841820  8841820        The recipe that creates blue, for example, inc...
8841821  8841821        On Independence Days of yore, old-timey crowds...
8841822  8841822        View full size image. Behind the scenes of the...

[8841823 rows x 3 columns]

In [ ]:
df_queries

_id                                               text
0       1185869  )what was the immediate impact of the success ...
1       1185868  _________ justice is designed to repair the ha...
2        597651                          what color is amber urine
3        403613  is autoimmune hepatitis a bile acid synthesis ...
4       1183785                                     elegxo meaning
...         ...                                                ...
509957   147073  difference between discrete and process manufa...
509958   243761                 how long did abraham lincoln serve
509959   162662       does adult acne rosacea give you blepharitis
509960   247194                       how long do you bake muffins
509961   195199                                     glioma meaning

[509962 rows x 2 columns]

In [ ]:
df_qrels_train

query-id  corpus-id  score
0        1185869          0      1
1        1185868         16      1
2         597651         49      1
3         403613         60      1
4        1183785        389      1
...          ...        ...    ...
532746     19285    8841362      1
532747    558837    4989159      1
532748    559149    8841547      1
532749    706678    8841643      1
532750    405466    8841735      1

[532751 rows x 3 columns]

In [ ]:
df_qrels_dev

query-id  corpus-id  score
0       300674    7067032      1
1       125705    7067056      1
2        94798    7067181      1
3         9083    7067274      1
4       174249    7067348      1
...        ...        ...    ...
7432    147073    8008770      1
7433    243761    8008787      1
7434    162662    8008977      1
7435    247194    8009319      1
7436    195199    8009377      1

[7437 rows x 3 columns]

In [ ]:
df_qrels_test

query-id  corpus-id  score
0        19335    1017759      0
1        19335    1082489      0
2        19335     109063      0
3        19335    1160863      0
4        19335    1160871      0
...        ...        ...    ...
9255   1133167    8839920      2
9256   1133167    8839922      2
9257   1133167     944810      0
9258   1133167     949411      0
9259   1133167     977421      0

[9260 rows x 3 columns]

In [ ]:
df_qrels_train['query-id'].value_counts()

query-id
574458     7
913949     7
199730     7
49751      7
47866      7
          ..
384305     1
979676     1
1042805    1
948363     1
405466     1
Name: count, Length: 502939, dtype: int64

In [ ]:
df_corpus_rn = df_corpus[['_id', 'text']].rename(columns={"_id": "corpus-id","text": "corpus"})
print(df_corpus_rn)
df_queries_rn = df_queries[['_id', 'text']].rename(columns={"_id": "query-id","text": "query"})
print(df_queries_rn)


         corpus-id                                             corpus
0                0  The presence of communication amid scientific ...
1                1  The Manhattan Project and its atomic bomb help...
2                2  Essay on The Manhattan Project - The Manhattan...
3                3  The Manhattan Project was the name for a proje...
4                4  versions of each volume as well as complementa...
...            ...                                                ...
8841818    8841818  When metal salts emit short wavelengths of vis...
8841819    8841819  Thousands of people across the United States w...
8841820    8841820  The recipe that creates blue, for example, inc...
8841821    8841821  On Independence Days of yore, old-timey crowds...
8841822    8841822  View full size image. Behind the scenes of the...

[8841823 rows x 2 columns]
        query-id                                              query
0        1185869  )what was the immediate impact of the success 

In [ ]:
df_qrels_train_final = df_qrels_train.merge(df_corpus_rn, on='corpus-id', how="left").merge(df_queries_rn, on='query-id', how="left")
print(df_qrels_train_final)
print()
df_qrels_dev_final = df_qrels_dev.merge(df_corpus_rn, on='corpus-id', how="left").merge(df_queries_rn, on='query-id', how="left")
print(df_qrels_dev_final)
print()
df_qrels_test_final = df_qrels_test.merge(df_corpus_rn, on='corpus-id', how="left").merge(df_queries_rn, on='query-id', how="left")
print(df_qrels_test_final)

        query-id  corpus-id  score  \
0        1185869          0      1   
1        1185868         16      1   
2         597651         49      1   
3         403613         60      1   
4        1183785        389      1   
...          ...        ...    ...   
532746     19285    8841362      1   
532747    558837    4989159      1   
532748    559149    8841547      1   
532749    706678    8841643      1   
532750    405466    8841735      1   

                                                   corpus  \
0       The presence of communication amid scientific ...   
1       The approach is based on a theory of justice t...   
2       Colorâurine can be a variety of colors, most...   
3       Inborn errors of bile acid synthesis can produ...   
4       The word convict here (elegcw /elegxo) means t...   
...                                                   ...   
532746  What is Anterolisthesis? Anterolisthesis is de...   
532747  Fly fishing in a river. Fly fishing is an angl.

## 数据集处理
query作为cond
corpus作为group
只处理train和dev,test先不管

In [ ]:
def handle(row):
    # query_id = row[0]
    cond = row[1]['query'].tolist()[0]
    group = row[1]['corpus'].tolist()
    return (cond, group)


### train

In [ ]:
name_group_list_train = [(name[0], group) for name, group in df_qrels_train_final.groupby(['query-id'])]
print(len(name_group_list_train))
print(len(name_group_list_train[0][1]))
print(name_group_list_train[1][1])
print(len(name_group_list_train[1][1]))

print("过滤后")
name_group_list_train_filter = list(filter(lambda _: len(_[1]) > 1, name_group_list_train))
print(len(name_group_list_train_filter))
print(len(name_group_list_train_filter[0][1]))
print(name_group_list_train_filter[1][1])
print(len(name_group_list_train_filter[1][1]))

502939
1
        query-id  corpus-id  score  \
395137         4    5613529      1   

                                                   corpus  \
395137  The formation of AA â Alcoholics Anonymous â...   

                                                    query  
395137   Defining alcoholism as a disease is associate...  
1
过滤后
25352
2
        query-id  corpus-id  score  \
280941       374    4086051      1   
280942       374    4086052      1   
280943       374    4086057      1   

                                                   corpus  \
280941  Quick Answer. The Internet was created essenti...   
280942  2003-06-30: the World Wide Web was invented by...   
280943  Tim Berners-Lee. The first web browser - or br...   

                                                    query  
280941  . what is the world wide web, when was it crea...  
280942  . what is the world wide web, when was it crea...  
280943  . what is the world wide web, when was it crea...  
3


In [ ]:
result_train = list(map(handle, name_group_list_train_filter))
result_train_df = pd.DataFrame(result_train, columns=['condition', 'group'])
result_train_df

condition  \
0                               +pregnant woman symptoms   
1      . what is the world wide web, when was it crea...   
2                  12 centimeters equals how many inches   
3                            1984 buick regal gear ratio   
4                             2% milk calories per glass   
...                                                  ...   
25347  why does carpal tunnel syndrome and the little...   
25348                             why do you need a will   
25349                          why do thunderstorms form   
25350                   why do the english say leftenant   
25351                        why did us declare war when   

                                                   group  
0      [Although the CDC states that pregnant women a...  
1      [Quick Answer. The Internet was created essent...  
2      [12 cm x (1 in./2.54 cm) = 4.7 inches multiply...  
3      [Read more. Although they are not listed speci...  
4      [An 8 ounce glass of whole milk contains appro...  
...                                                  ...  
25347  [Carpal tunnel syndrome can cause tingling, nu...  
25348  [If you want to leave any part of your assets ...  
25349  [How do they form? Thunderstorms are formed by...  
25350  [It's only the difference in pronunciation. In...  
25351  [The United States declared war on Germany for...  

[25352 rows x 2 columns]

In [ ]:
sum(map(lambda _: len(_[1]), name_group_list_train_filter))

55164

### test

In [ ]:
name_group_list_dev = [(name[0], group) for name, group in df_qrels_dev_final.groupby(['query-id'])]
print(len(name_group_list_dev))
print(len(name_group_list_dev[0][1]))
print(name_group_list_dev[1][1])
print(len(name_group_list_dev[1][1]))

print("过滤后")
name_group_list_dev_filter = list(filter(lambda _: len(_[1]) > 1, name_group_list_dev))
print(len(name_group_list_dev_filter))
print(len(name_group_list_dev_filter[0][1]))
print(name_group_list_dev_filter[1][1])
print(len(name_group_list_dev_filter[1][1]))

6980
1
      query-id  corpus-id  score  \
2655      1215    7395960      1   

                                                 corpus  \
2655  In Canada, there are 3 levels of government. E...   

                                                  query  
2655  3 levels of government in canada and their res...  
1
过滤后
390
2
      query-id  corpus-id  score  \
4136      4947    7581255      1   
4137      4947    7581263      1   

                                                 corpus               query  
4136  $25 Million. Ludacris net worth: Award winning...  Ludacris Net Worth  
4137  Ludacris net worth is estimated at $25 million...  Ludacris Net Worth  
2


In [ ]:
result_dev = list(map(handle, name_group_list_dev_filter))
result_dev_df = pd.DataFrame(result_dev, columns=['condition', 'group'])
result_dev_df

condition  \
0    Explain what a bone scan is and what it is use...   
1                                   Ludacris Net Worth   
2        age not to take off shoes at airline security   
3                  aplastic anemia causes and symptoms   
4                               asus phones price list   
..                                                 ...   
385                         hazel haskett in real life   
386                    foods to keep constipation away   
387                         effects of using pedialyte   
388                                diff types of fuses   
389                             definition of shagreen   

                                                 group  
0    [Why It Is Done. A bone scan is done to: 1  Fi...  
1    [$25 Million. Ludacris net worth: Award winnin...  
2    [Itâs a victory for old soles. Travelers ove...  
3    [Symptoms and Complications. Symptoms of aplas...  
4    [More about Asus Mobiles Price List in India. ...  
..                                                 ...  
385  [Hazel Haskett is the young heroine of Dolphin...  
386  [Focus on soluble fiber instead. Keep in mind ...  
387  [Plus, if youâre aiming for weight loss, the...  
388  [Automotive fuses are a class of fuses used to...  
389  [What is Shagreen Shagreen is an exotic materi...  

[390 rows x 2 columns]

### 处理上传

In [ ]:
! pip install datasets

In [ ]:
from datasets import Dataset, DatasetDict
from huggingface_hub import login, create_repo

In [ ]:
dataset_train = Dataset.from_pandas(result_train_df)
dataset_dev = Dataset.from_pandas(result_dev_df)

In [ ]:
dataset_dict = DatasetDict({
    "train": dataset_train,
    "validation": dataset_dev
})
dataset_dict

DatasetDict({
    train: Dataset({
        features: ['condition', 'group'],
        num_rows: 25352
    })
    validation: Dataset({
        features: ['condition', 'group'],
        num_rows: 390
    })
})

In [ ]:
login(token="")

In [ ]:
# 创建数据集仓库
repo_id = "bcai001/c-sts-msmarco-query-as-condition-group-as-pos"  # 例如: "johnsmith/sentiment-analysis-data"
create_repo(repo_id, repo_type="dataset", exist_ok=True)

# 上传数据集
dataset_dict.push_to_hub(repo_id, private=True)

print(f"Dataset uploaded to: https://huggingface.co/datasets/{repo_id}")

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/26 [00:00<?, ?ba/s]

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Dataset uploaded to: https://huggingface.co/datasets/bcai001/c-sts-msmarco-query-as-condition-group-as-pos
